# KDE Sampling

police.uk data has high (perturbed?) spatial resolution but very poor temporal (month of occurrence) and only broad categorical resolution:

- Other theft
- Violence and sexual offences
- Bicycle theft
- Criminal damage and arson
- Public order
- Robbery
- Shoplifting
- Vehicle crime
- Drugs
- Possession of weapons
- Theft from the person
- Burglary
- Other crime

This notebook creates a Kernel Density Estimate (KDE) over an entire force area, for one of the above crime categories, using 3 years data.

Synthetic crimes can then be sampled from this spatial distribution


In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from functools import partial

import geopandas as gpd
import numpy as np
from scipy.stats import gaussian_kde

from utils import CATEGORIES, extract_crime_data, get_lsoa_boundaries

In [ ]:
rng = np.random.default_rng(19937)

CATEGORY = CATEGORIES[2]
crime_data = extract_crime_data("./data/wy202204-202503.zip")
# filter by catgegory and remove any points
crime_data = crime_data[(crime_data["Crime type"] == CATEGORY)]
crime_data

Month  \
Crime ID                                                      
298e807de56cd30acd92aeaae0530b24252a2ba0fb5041a...  2022-04   
b4cdb65818f3c72c99e878bc1cf9dd12105ac362c08f20a...  2022-04   
c1b07eecc81cce4f3d874cd085bf5a18fb9ad82abb06674...  2022-04   
8fb8e069000240559159390651104a297b75d6234a6c120...  2022-04   
3138d50e8e27c26500c72ba5d1700d09a091746ac4f5a9d...  2022-04   
...                                                     ...   
e64c0683ab4d06814a96805a4cb4681874aeb9d912d89ba...  2025-03   
6837eb184f8b046caadee5e771638f6b948972063ec2b94...  2025-03   
678e9eac568c6bd03e48cc61cea462184332d04d7fc726c...  2025-03   
b1696b6815931851c0f41568cd98c6b93b8f50bbb9c4e8b...  2025-03   
8d60513259b69aae5b12641d30b51f873c1fbf1104d04b7...  2025-03   

                                                              Reported by  \
Crime ID                                                                    
298e807de56cd30acd92aeaae0530b24252a2ba0fb5041a...  West Yorkshire Police   
b4cdb65818f3c72c99e878bc1cf9dd12105ac362c08f20a...  West Yorkshire Police   
c1b07eecc81cce4f3d874cd085bf5a18fb9ad82abb06674...  West Yorkshire Police   
8fb8e069000240559159390651104a297b75d6234a6c120...  West Yorkshire Police   
3138d50e8e27c26500c72ba5d1700d09a091746ac4f5a9d...  West Yorkshire Police   
...                                                                   ...   
e64c0683ab4d06814a96805a4cb4681874aeb9d912d89ba...  West Yorkshire Police   
6837eb184f8b046caadee5e771638f6b948972063ec2b94...  West Yorkshire Police   
678e9eac568c6bd03e48cc61cea462184332d04d7fc726c...  West Yorkshire Police   
b1696b6815931851c0f41568cd98c6b93b8f50bbb9c4e8b...  West Yorkshire Police   
8d60513259b69aae5b12641d30b51f873c1fbf1104d04b7...  West Yorkshire Police   

                                                             Falls within  \
Crime ID                                                                    
298e807de56cd30acd92aeaae0530b24252a2ba0fb5041a...  West Yorkshire Police   
b4cdb65818f3c72c99e878bc1cf9dd12105ac362c08f20a...  West Yorkshire Police   
c1b07eecc81cce4f3d874cd085bf5a18fb9ad82abb06674...  West Yorkshire Police   
8fb8e069000240559159390651104a297b75d6234a6c120...  West Yorkshire Police   
3138d50e8e27c26500c72ba5d1700d09a091746ac4f5a9d...  West Yorkshire Police   
...                                                                   ...   
e64c0683ab4d06814a96805a4cb4681874aeb9d912d89ba...  West Yorkshire Police   
6837eb184f8b046caadee5e771638f6b948972063ec2b94...  West Yorkshire Police   
678e9eac568c6bd03e48cc61cea462184332d04d7fc726c...  West Yorkshire Police   
b1696b6815931851c0f41568cd98c6b93b8f50bbb9c4e8b...  West Yorkshire Police   
8d60513259b69aae5b12641d30b51f873c1fbf1104d04b7...  West Yorkshire Police   

                                                                          Location  \
Crime ID                                                                             
298e807de56cd30acd92aeaae0530b24252a2ba0fb5041a...        On or near Wheatley Road   
b4cdb65818f3c72c99e878bc1cf9dd12105ac362c08f20a...        On or near Wheatley Road   
c1b07eecc81cce4f3d874cd085bf5a18fb9ad82abb06674...        On or near Pattie Street   
8fb8e069000240559159390651104a297b75d6234a6c120...   On or near Greenthwaite Close   
3138d50e8e27c26500c72ba5d1700d09a091746ac4f5a9d...          On or near East Parade   
...                                                                            ...   
e64c0683ab4d06814a96805a4cb4681874aeb9d912d89ba...        On or near Nelson Street   
6837eb184f8b046caadee5e771638f6b948972063ec2b94...    On or near Jacob'S Well Lane   
678e9eac568c6bd03e48cc61cea462184332d04d7fc726c...          On or near Frain Close   
b1696b6815931851c0f41568cd98c6b93b8f50bbb9c4e8b...  On or near Park Lodge Crescent   
8d60513259b69aae5b12641d30b51f873c1fbf1104d04b7...        On or near Lilley Street   

                                                    LSOA code       LSOA name  \
Crime ID                      

In [9]:
lsoa_boundaries = get_lsoa_boundaries("FE", overlapping=crime_data)
lsoa_boundaries

LSOA21NM LSOA21NMW   BNG_E   BNG_N      LAT     LONG  \
LSOA21CD                                                               
E01010568  Bradford 016A      None  416258  438952  53.8466 -1.75438   
E01010569  Bradford 016B      None  414693  438453  53.8421 -1.77819   
E01010571  Bradford 016C      None  415223  438398  53.8416 -1.77013   
E01010572  Bradford 016D      None  415428  438857  53.8457 -1.76700   
E01010573  Bradford 013A      None  414123  440131  53.8572 -1.78677   
...                  ...       ...     ...     ...      ...      ...   
E01035048     Leeds 099G      None  430979  428149  53.7488 -1.53171   
E01035050     Leeds 105G      None  430214  426790  53.7366 -1.54345   
E01035051     Leeds 105H      None  431335  427174  53.7400 -1.52641   
E01035052     Leeds 105I      None  431014  426532  53.7343 -1.53135   
E01035054     Leeds 112F      None  430907  432531  53.7882 -1.53237   

                                       GlobalID  \
LSOA21CD                                          
E01010568  137e4959-a6d1-40d7-b2a5-563c9ff4af20   
E01010569  1f4e6cbc-75a9-4ffa-b851-0792627c632e   
E01010571  1894828c-0aae-4ded-8e36-77a62ab8c4b4   
E01010572  9a46128a-3965-45d7-b06f-e6f2af85bbb1   
E01010573  25d2a550-da16-4b04-99ed-16404376537c   
...                                         ...   
E01035048  3402834e-dade-45d4-b600-835a4a7d8bea   
E01035050  607700e7-4a88-4736-9f01-e26e4347dc5d   
E01035051  96961ba7-331b-4410-ac81-6d58fc3cbe31   
E01035052  9cd4244a-8d53-4af2-8362-1f9898de0a65   
E01035054  843ce5f4-2571-42c8-867c-2b280fe96f4a   

                                                    geometry  
LSOA21CD                                                      
E01010568  POLYGON ((416422.17 439366.289, 416417.848 439...  
E01010569  POLYGON ((415369.043 439212.461, 415368.435 43...  
E01010571  POLYGON ((415768.621 438654.729, 415766.728 43...  
E01010572  POLYGON ((415616.807 439194.596, 415622.818 43...  
E01010573  POLYGON ((414068.435 441336.988, 414070 441336...  
...                                                      ...  
E01035048  POLYGON ((431362 428526, 431366 428520, 431369...  
E01035050  POLYGON ((430986.896 427756.226, 430982.739 42...  
E01035051  POLYGON ((431044.305 427760.241, 431050.502 42...  
E01035052  POLYGON ((431312.508 427066, 431277.221 426958...  
E01035054  POLYGON ((430657.956 433169.095, 430686 433160...  

[1138 rows x 8 columns]

In [33]:
# create the KDE
def kde_bandwidth(obj, *, fac: float = 0.2) -> float:
    """We use Scott's Rule, multiplied by a constant factor."""
    return np.power(obj.n, -1.0 / (obj.d + 4)) * fac


points = np.array(crime_data.geometry.map(lambda p: [p.y, p.x]).tolist()).T
# kde = gaussian_kde(
#     points, 0.01
# )  # values greater than this produce samples that are too "spread out"

kde = gaussian_kde(points, bw_method=partial(kde_bandwidth, fac=0.2))

In [41]:
# Create synthetic data
n_crimes = min(len(crime_data), 10000)

y, x = kde.resample(n_crimes, seed=rng.integers(2**32))
synth_crime = gpd.GeoDataFrame(
    index=range(n_crimes),
    data={
        "Month": None,
        "Reported by": "Officer Alex James Murphy",
        "Falls within": "West Yorkshire Police",
        "Location": None,
        "Crime type": CATEGORY,
    },
    geometry=gpd.points_from_xy(x, y),
    crs="epsg:27700",
)
# spatial join to get LSOA from point
synth_crime = gpd.sjoin(synth_crime, lsoa_boundaries[["LSOA21NM", "geometry"]], how="left").rename(
    columns={"LSOA21CD": "LSOA code", "LSOA21NM": "LSOA name"}
)

In [42]:
# overlay the same number of real crimes on sampled crimes.
map = synth_crime.explore(color="red")
map = crime_data.sample(n_crimes, replace=False).explore(m=map)

map

In [ ]:
#